# Génération des réseaux à partir des règles et d'un jeu d'essai de formes

Il faut décider de la place des corrections phonologiques dans le traitement et dans l'évaluation.

- Swim1 basé sur les règles de l'échantillon initial
    - Phon : 
        - sans correction phonologique
        - avec correction phonologique
    - Gén-1 : génération des formes d'après les contextes phonologiques
    - Gén-2 : génération du réseau d'après les contextes phonologiques
    - Filt-1 : extraction du sous-réseau symétrique
    - Filt-2 : génération du réseau non-orienté correspondant à Filt-1
    - Filt-3 : extraction des cliques maximales & fidèles
 
- Swim2 basé sur le réseau calculé par Swim1
    - Exp : génération d'un nouvel échantillon basé sur Swim1
        - Phon :
             - sans correction phonologique
             - avec correction phonologique
    - Gén-1 : génération des formes sans contexte phonologique
    - Gén-2 : génération du réseau sans contexte phonologique
    - Filt-1 : extraction du sous-réseau symétrique
    - Filt-2 : génération du réseau non-orienté correspondant à Filt-1
    - Filt-3 : extraction des cliques maximales & fidèles
- Évaluation
    - Phon :
        - sans correction phonologique
        - avec correction phonologique

## Importations
- codecs pour les encodages
- pandas et numpy pour les calculs sur tableaux
- matplotlib pour les graphiques
- itertools pour les itérateurs sophistiqués (paires sur liste, ...)

<a id="top"></a>

Liens :
- [top](#top)
- [finRegles](#finRegles)
- [laverForms](#laverForms)

In [1]:
# -*- coding: utf8 -*-
import codecs,operator,datetime,os,glob,cellbell
import features
import re
import pandas as pd
from openpyxl import load_workbook
import numpy as np
import matplotlib.pyplot as plt
import itertools as it
import pickle
import networkx as nx
#%pylab inline
#pd.options.display.mpl_style = 'default'
debug=False
from __future__ import print_function
from IPython.display import display

from FrenchPhonology import makeFrench,setNeutralisation,normalizePhono
import SWiM_Utils as SwimU
import SWiM_Network as SwimN
from SWiM_Utils import *
from SWiM_Network import *
from EspacesThematiques import etCols

def dateheure(f="%y/%m/%d %H:%M"):
    return datetime.datetime.utcnow().strftime(f) # %y%m%d%H%M

colsParadigme=["lexeme"]+etCols
# colsParadigme

S Z N J ê ô â r E H O 6 9 2


### Préparation des matrices de traits

In [2]:
features.add_config('bdlexique.ini')
fs=features.FeatureSystem('phonemes')
tableNeutralise=setNeutralisation("NS")

# Lecture du Jeu d'essai
- chargement du fichier
    - trialFormes
    - listeTest
- normalisation de la phonologie

Liste des lexèmes dans le jeu d'essai
- Sans doute inefficace
    - un lexème peut apparaître plusieurs dans le jeu d'essai avec des lexicalisations différentes

Liste des cases dans le jeu d'essai

## Normalisation des entrées

⚠️ Attention, la normalisation des entrées interagit avec l'analyse déjà faite. Il faut rester cohérent avec le codage utilisé pour la génération des règles

In [3]:
# trialFormes=normalizePhono(trialFormes,tableNeutralise)

# Choix des règles
⚠️ pour charger les règles PKL, il faut avoir [déclaré les classes correspondantes](https://www.stefaanlippens.net/python-pickling-and-dealing-with-attributeerror-module-object-has-no-attribute-thing.html)

- *rulesPrefix* est une partie du nom des règles

Si les règles sont basées sur des morphomes, il faut créer une correspondance entre morphomes et cases :
- dictMorphomeCases pour remplir le paradigme après traitement

In [4]:
def prefixRules(numero,sampleType="",casesType=""):
    candidats=[]
    matchFile=ur"(^.*/Longitudinal-%s-T\d+-F\d+%s)-Regles\.pkl"%(numero,sampleType+casesType)
#     matchFile=ur"^.*/Longitudinal-Lexique3(-%s-T\d+-F\d+)%s\.pkl"%(numero,sampleType+casesType)
    print (matchFile)
    for sample in rulesFiles:
        m=re.match(matchFile,sample)
        if m:
#            print (sample)
#            print (m.group(1))
            candidats.append(m.group(1))
    if len(candidats)==1:
        print (candidats[0])
        return candidats[0]
    else:
        print ("PB pas de nom unique correspondant",len(candidats),numero,sampleType,casesType)

<a id="choixSample"></a>

In [5]:
def nb2Mesure(strNb):
    nbMesures={0:"",1:"k",2:"M",3:"G"}
    result=strNb
    m=re.match(ur"^([0-9]*?)(0+)$",result)
    if m:
        nbZeros=len(m.group(2))
        result=u"%s%s"%(m.group(1)+"0"*(nbZeros%3),nbMesures[nbZeros//3])
    return result

In [6]:
def getRules(sampleNumero,sampleType,casesType):
    rulesPrefix=prefixRules(sampleNumero,sampleType,casesType)
    m=re.search(ur"-T(\d+)-",rulesPrefix)
    if m:
        nbTokensBrut=m.group(1)
        nbTokens=nb2Mesure(nbTokensBrut)
        print (nbTokens)
    else:
        print ("no Tokens")
    with open(rulesPrefix+'-Regles.pkl', 'rb') as input:
        analyseRules = pickle.load(input)
    return (analyseRules,rulesPrefix,nbTokens)

# Analyse des morphomes

In [7]:
def makeMorphomeMaps(rulesPrefix):
    if "Morphome" in casesType:
        baseMap=pd.read_pickle(rulesPrefix+'.pkl').groupby("morphome")["case"].first().to_dict()
        msp2omp={}
        omp2msp={}
        for k in baseMap:
            mspCases=k.split("/")
            ompCase=baseMap[k]
            for case in mspCases:
                msp2omp[case]=ompCase
                if ompCase not in omp2msp:
                    omp2msp[ompCase]=[]
                omp2msp[ompCase].append(case)
    else:
        msp2omp={case:case for case in analyseCases}
        omp2msp={case:[case] for case in analyseCases}
    return (msp2omp,omp2msp)

In [8]:
def formes2Morphomes(df):
    lDF=df.copy()
    for c in msp2omp:
        lDF.columns=lDF.columns.str.replace(c,msp2omp[c])
    return lDF.stack().unstack()

def morphomes2Formes(df):
    lDF=df.copy()
    for m in omp2msp:
        for c in omp2msp[m]:
            lDF[c]=lDF[m]
    for c in (set(etCols)-set(msp2omp.keys())):
        lDF[c]=np.NaN
    return lDF

# Lecture du Gold
- chargement du fichier
- normalisation de la phonologie

In [9]:
goldPrefix="/Users/gilles/pCloud Drive/FOD/GB/2015-Data/"
goldFile="MGC-171229-Verbes3.pkl"
lexiqueGold=pd.read_pickle(path=goldPrefix+goldFile)

In [10]:
'''Rectifications phonologiques'''
lexiqueGold["phono"]=lexiqueGold["phono"].apply(lambda x: makeFrench(x,tableNeutralise))
completeParadigmes=pd.pivot_table(lexiqueGold, values='phono', index=['lexeme'], columns=['case'], aggfunc=lambda x: ",".join(x)).reset_index().reindex()
completeParadigmes

case         lexeme         ai1P        ai1S         ai2P        ai2S  \
0          abaisser       abEsam       abEsE       abEsat       abEsa   
1        abandonner     abâdOnam     abâdOnE     abâdOnat     abâdOna   
2        abasourdir    abazurdim    abazurdi    abazurdit    abazurdi   
3           abattre       abatim       abati       abatit       abati   
4           abcéder      absEdam      absEdE      absEdat      absEda   
5          abdiquer      abdikam      abdikE      abdikat      abdika   
6          abecquer       abEkam       abEkE       abEkat       abEka   
7           aberrer       abEram       abErE       abErat       abEra   
8          abhorrer       abOram       abOrE       abOrat       abOra   
9           abjurer      abZyram      abZyrE      abZyrat      abZyra   
10          ablater      ablatam      ablatE      ablatat      ablata   
11          ablatir      ablatim      ablati      ablatit      ablati   
12         abloquer      ablOkam      ablOkE      ablOkat      ablOka   
13           abolir       abOlim       abOli       abOlit       abOli   
14          abonder       abôdam       abôdE       abôdat       abôda   
15          abonner       abOnam       abOnE       abOnat       abOna   
16          abonnir       abOnim       abOni       abOnit       abOni   
17          aborder      abOrdam      abOrdE      abOrdat      abOrda   
18          aborner      abOrnam      abOrnE      abOrnat      abOrna   
19         aboucher       abuSam       abuSE       abuSat       abuSa   
20          abouler       abulam       abulE       abulat       abula   
21          abouter       abutam       abutE       abutat       abuta   
22          aboutir       abutim       abuti       abutit       abuti   
23           aboyer      abwajam      abwajE      abwajat      abwaja   
24          abraser      abrazam      abrazE      abrazat      abraza   
25         abreuver      abr9vam      abr9vE      abr9vat      abr9va   
26        abricoter    abrikOtam    abrikOtE    abrikOtat    abrikOta   
27          abriter      abritam      abritE      abritat      abrita   
28          abroger      abrOZam      abrOZE      abrOZat      abrOZa   
29          abrutir      abrytim      abryti      abrytit      abryti   
...             ...          ...         ...          ...         ...   
6531      étreindre      EtrEJim      EtrEJi      EtrEJit      EtrEJi   
6532       étrenner      EtrEnam      EtrEnE      EtrEnat      EtrEna   
6533       étriller      Etrijam      EtrijE      Etrijat      Etrija   
6534        étriper      Etripam      EtripE      Etripat      Etripa   
6535       étriquer      Etrikam      EtrikE      Etrikat      Etrika   
6536        étrécir      EtrEsim      EtrEsi      EtrEsit      EtrEsi   
6537  étrésillonner  EtrEzijOnam  EtrEzijOnE  EtrEzijOnat  EtrEzijOna   
6538        étudier      Etydjam      EtydjE      Etydjat      Etydja   
6539         étuver       Etyvam       EtyvE       Etyvat       Etyva   
6540         étêter       EtEtam       EtEtE       EtEtat       EtEta   
6541        évacuer     EvakyHam     EvakyHE     EvakyHat     EvakyHa   
6542         évader       Evadam       EvadE       Evadat       Evada   
6543        évaluer     EvalyHam     EvalyHE     EvalyHat     EvalyHa   
6544    évangéliser   EvâZElizam   EvâZElizE   EvâZElizat   EvâZEliza   
6545       évanouir     Evanuwim     Evanuwi     Evanuwit     Evanuwi   
6546       évaporer     EvapOram     EvapOrE     EvapOrat     EvapOra   
6547         évaser       Evazam       EvazE       Evazat       Evaza   
6548       éveiller       EvEjam       EvEjE       EvEjat       EvEja   
6549        éventer       Evâtam       EvâtE       Evâtat       Evâta   
6550     éventiller     Evâtijam     EvâtijE     Evâtijat     Evâtija   
6551       éventrer      Evâtram      EvâtrE      Evâtrat      Evâtra   
6552       évertuer    EvErtyHam    EvErtyHE    EvErtyHat    EvErtyHa   
6553         évider       Evidam       EvidE       Evidat 

# Coloration

In [76]:
def colorCells(row,dfPar):
    
    def compareGenGold(genCase,goldCase):
        result=""
        if goldCase==goldCase:
            genSet=set(genCase.split(","))
            goldSet=set(goldCase.split(","))
            if genSet==goldSet:
                result="equal"
            elif genSet&goldSet==goldSet:
                result="goldSet"
            elif genSet&goldSet==genSet:
                result="genSet"
            elif genSet&goldSet!=set():
                result="intersect"
            else:
                result="different"
        else:
            result="noGold"
        return result
    
    
    def getCellColor(surForme):
        result=""
        origForme=dfPar.iloc[iLexeme][case]
#         if case=="pi3S":
#             print (u"entrée getCellColor >",case, surForme)
#             print ("origForme",origForme)
#             print (dfPar.iloc[iLexeme])
        if origForme==origForme and surForme in origForme.split(","):
            result="blue"
        elif case in casesPar:
            lCase=msp2omp[case] # gérer les cases morphomiques
            genCase=makeFrench(row[lCase],tableNeutralise)
#             if "," in genCase:
#                 print(", in genCase")
            compGenGold=compareGenGold(genCase,goldCase)
            if compGenGold=="equal":
                compRowGold=compareGenGold(row[lCase],goldCase)
                if compRowGold=="equal":
                    result="green"
                else:
                    result="#66CC33"
            elif compGenGold=="genSet":
                result="#CCCC33"
            elif compGenGold=="goldSet":
                result="#FF33FF"
            elif compGenGold=="intersect":
                result="#669900"
            elif compGenGold=="noGold":
                result="#CCCCCC"
            else:
                result="red"
#             else:
#                 if genCase==goldCase:
#                     if row[lCase]==goldCase:
#                         result="green"
#                     else:
#                         result="#90EE90"
#                 elif goldCase==goldCase:
#                     result="red"
        else:
            result="#333333"
        return result

    def pickCellColor(cellColors):
        cellColor=""
        lColors=list(set(cellColors))
        if len(lColors)==1:
            cellColor=lColors[0]
        else:
            if "blue" in lColors:
                cellColor="#0066CC"
            elif "green" in lColors:
                if "red" in lColors:
                    cellColor="orange"
                elif "#90EE90" in lColors:
                    cellColor="#90EE90"
                else:
                    cellColor="#FF33FF"
            else:
                cellColor="#FF33FF"
        return cellColor
                
    result=[""] # style pour la colonne lexeme
    lexeme=row["lexeme"]
    iLexeme=row.name
    casesRow=row.index.tolist()
    casesRow.remove("lexeme")
    casesPar=dfPar.columns.tolist()
    for case in casesRow:
        goldCaseValue=goldTestForms.loc[goldTestForms.index==lexeme+"-"+case,"value"]
        if len(goldCaseValue)==0:
            goldCase=np.NaN
        else:
            goldCase=goldCaseValue.values[0]
        if row[case]==row[case]: # si row[case] n'est pas np.NaN
            if "," in row[case]:
                rowColors=[]
                for r in row[case].split(","):
#                     print ("getCellColor ?",case,r)
                    rowColor=getCellColor(r)
#                     print ("getCellColor :",rowColor)
                    rowColors.append(rowColor)
#                 print (lexeme,case,rowColors)
                rowColor=pickCellColor(rowColors)
                result.append('background-color: %s'%rowColor)
            else: 
                rowColor=getCellColor(row[case])
                result.append('background-color: %s'%rowColor)
#                 if case in casesPar and row[case]==dfPar.iloc[iLexeme][case]:
#                     result.append('background-color: blue')
#                 elif case in casesPar:
#                     lCase=msp2omp[case] # gérer les cases morphomiques
#                     genCase=makeFrench(row[lCase],tableNeutralise)
#                     if genCase==goldCase:
#                         if row[lCase]==goldCase:
#                             result.append('background-color: green')
#                         else:
#                             result.append('background-color: #90EE90')
#                     elif goldCase==goldCase:
#                         result.append('background-color: red')
#                     else:
#                         result.append('background-color: orange')
        else:
            if goldCase==goldCase:
                result.append('background-color: yellow')
            else:
                result.append('background-color: white')
    return result


In [12]:
def getWriterXLSX(fn):
    try:
        bookResult = load_workbook(fn)
        writerResult = pd.ExcelWriter(fn, engine='openpyxl')
        writerResult.book=bookResult
        writerResult.sheets = dict((ws.title, ws) for ws in bookResult.worksheets)
    except:
        writerResult = pd.ExcelWriter(fn, engine='openpyxl')
    return writerResult


<a id="finRegles"></a>
# SWIM1

Liens :
- [top](#top)
- [finRegles](#finRegles)
- [laverForms](#laverForms)

In [ ]:
sampleNumeros="00 09 19 29 39 49 50 51 52 53 54 64 74 84 94 95 96 97 98 99 109 119 120 121 122 123 124 125 126".split(" ")
# sampleNumeros=["39"]
sampleType="-X"
casesType="-Morphomes"
#sampleType=""
# casesType=""

# Choix du jeu d'essai
trialPrefix="/Users/gilles/ownCloud/Recherche/Boye/HDR/Memoire/Longitudinales/"
trialFile="JeuEssai-G1.csv"
trialFormes0=pd.read_csv(trialPrefix+trialFile,sep=";",encoding="utf8")

# Liste des lexèmes du jeu d'essai
trialLexemes=trialFormes0.lexeme.unique().tolist()

# Faire la liste des PKL
rulesRep="/Users/gilles/pCloud Drive/FOD/GB/2015-Data/Longitudinales/"
rulesFiles=glob.glob(rulesRep+"*.pkl")


# Préparation du Gold général
goldTestForms=pd.melt(completeParadigmes[completeParadigmes["lexeme"].isin(trialLexemes)],id_vars=["lexeme"]).dropna()
goldTestForms["lexeme-case"]=goldTestForms["lexeme"]+"-"+goldTestForms["case"]
goldTestForms.drop(labels=["lexeme","case"],axis=1,inplace=True)
goldTestForms.set_index(["lexeme-case"],inplace=True)
goldTestForms=normalizePhono(goldTestForms,tableNeutralise)

# Boucle sur les différents jeux de règles
print (dateheure())
for sampleNumero in sampleNumeros:
    # Sélectionner les règles pour SwimN
    (analyseRules,rulesPrefix,nbTokens)=getRules(sampleNumero,sampleType,casesType)
    SwimN.analyseRules=analyseRules
    
    # Faire la liste des cases concernées par les règles pour SwimN
    analyseCases=list(set([c1 for (c1,c2) in analyseRules.keys()]))
    SwimN.analyseCases=analyseCases
    
    # Calculer les correspondances entre MSP et OMP
    (msp2omp,omp2msp)=makeMorphomeMaps(rulesPrefix)
    SwimN.omp2msp=omp2msp
    SwimN.msp2omp=msp2omp

    # Regrouper les formes initiales selon l'OMP correspondant aux règles
    trialFormes=formes2Morphomes(trialFormes0)
    
    # Calculer le résultat de SWiM1 (analogies sur les trialFormes avec contexte phonologique)
    trialGen1=generateFromTrial(trialFormes,contextFree=False)
    result1=morphomes2Formes(trialGen1)[colsParadigme].style.apply(lambda x: colorCells(x,trialFormes0),axis=1)
    display(result1)
    
    # Calculer le résultat de SWiM2 (analogies sur le résultat de SWiM1 sans contexte phonologique)
    trialGen2=generateFromTrial(formes2Morphomes(trialGen1),contextFree=True)
    result2=morphomes2Formes(trialGen2)[colsParadigme].style.apply(lambda x: colorCells(x,trialFormes0),axis=1)
    display(result2)
    
    trialResult=trialPrefix+trialFile.replace(".csv",".xlsx")
    writerResult=getWriterXLSX(trialResult)
    result2.to_excel(writerResult,sheet_name=u"%s%s%s"%(nbTokens,sampleType,casesType))
    writerResult.save()
print (dateheure())

20/09/06 16:32
(^.*/Longitudinal-00-T\d+-F\d+-X-Morphomes)-Regles\.pkl
/Users/gilles/pCloud Drive/FOD/GB/2015-Data/Longitudinales/Longitudinal-00-T10000-F3663-X-Morphomes
10k


(^.*/Longitudinal-09-T\d+-F\d+-X-Morphomes)-Regles\.pkl
/Users/gilles/pCloud Drive/FOD/GB/2015-Data/Longitudinales/Longitudinal-09-T100000-F14858-X-Morphomes
100k


(^.*/Longitudinal-19-T\d+-F\d+-X-Morphomes)-Regles\.pkl
/Users/gilles/pCloud Drive/FOD/GB/2015-Data/Longitudinales/Longitudinal-19-T200000-F20877-X-Morphomes
200k


(^.*/Longitudinal-29-T\d+-F\d+-X-Morphomes)-Regles\.pkl
/Users/gilles/pCloud Drive/FOD/GB/2015-Data/Longitudinales/Longitudinal-29-T300000-F25250-X-Morphomes
300k


(^.*/Longitudinal-39-T\d+-F\d+-X-Morphomes)-Regles\.pkl
/Users/gilles/pCloud Drive/FOD/GB/2015-Data/Longitudinales/Longitudinal-39-T400000-F28522-X-Morphomes
400k


...

(^.*/Longitudinal-84-T\d+-F\d+-X-Morphomes)-Regles\.pkl
/Users/gilles/pCloud Drive/FOD/GB/2015-Data/Longitudinales/Longitudinal-84-T4000000-F57148-X-Morphomes
4M


(^.*/Longitudinal-94-T\d+-F\d+-X-Morphomes)-Regles\.pkl
/Users/gilles/pCloud Drive/FOD/GB/2015-Data/Longitudinales/Longitudinal-94-T5000000-F59398-X-Morphomes
5M


(^.*/Longitudinal-95-T\d+-F\d+-X-Morphomes)-Regles\.pkl
/Users/gilles/pCloud Drive/FOD/GB/2015-Data/Longitudinales/Longitudinal-95-T6000000-F61082-X-Morphomes
6M


(^.*/Longitudinal-96-T\d+-F\d+-X-Morphomes)-Regles\.pkl
/Users/gilles/pCloud Drive/FOD/GB/2015-Data/Longitudinales/Longitudinal-96-T7000000-F62451-X-Morphomes
7M


(^.*/Longitudinal-97-T\d+-F\d+-X-Morphomes)-Regles\.pkl
/Users/gilles/pCloud Drive/FOD/GB/2015-Data/Longitudinales/Longitudinal-97-T8000000-F63534-X-Morphomes
8M


In [72]:
trialGen1.iloc[2]
goldTestForms[goldTestForms.index.str.contains("aboyer")]

value
lexeme-case           
aboyer-ai1P    abwajam
aboyer-ai1S     abwajE
aboyer-ai2P    abwajat
aboyer-ai2S     abwaja
aboyer-ai3P    abwajEr
aboyer-ai3S     abwaja
aboyer-fi1P     abwarô
aboyer-fi1S     abwarE
aboyer-fi2P     abwarE
aboyer-fi2S     abwara
aboyer-fi3P     abwarô
aboyer-fi3S     abwara
aboyer-ii1P     abwajô
aboyer-ii1S     abwajE
aboyer-ii2P     abwajE
aboyer-ii2S     abwajE
aboyer-ii3P     abwajE
aboyer-ii3S     abwajE
aboyer-inf      abwajE
aboyer-is1P  abwajasjô
aboyer-is1S    abwajas
aboyer-is2P  abwajasjE
aboyer-is2S    abwajas
aboyer-is3P    abwajas
aboyer-is3S     abwaja
aboyer-pI1P     abwajô
aboyer-pI2P     abwajE
aboyer-pI2S       abwa
aboyer-pP       abwajâ
aboyer-pc1P    abwarjô
aboyer-pc1S     abwarE
aboyer-pc2P    abwarjE
aboyer-pc2S     abwarE
aboyer-pc3P     abwarE
aboyer-pc3S     abwarE
aboyer-pi1P     abwajô
aboyer-pi1S       abwa
aboyer-pi2P     abwajE
aboyer-pi2S       abwa
aboyer-pi3P       abwa
aboyer-pi3S       abwa
aboyer-ppMS     abwajE
aboyer-ps1P     abwajô
aboyer-ps1S       abwa
aboyer-ps2P     abwajE
aboyer-ps2S       abwa
aboyer-ps3P       abwa
aboyer-ps3S       abwa

Liens :
- [top](#top)
- [choix sample](#choixSample)

# To Do
1. gérer les morphomes => fait
- colorer les formes en sortie => fait
- gérer les cliques ex-aequo
- gérer une boucle pour les échantillons => en cours, vérifier les conditions initiales


# Fin du traitement